(ch:fundamentals_of_ml)=
# 최적화와 일반화

**감사의 글**

아래 내용은 프랑소와 숄레의 
[Deep Learning with Python(2판)](https://github.com/fchollet/deep-learning-with-python-notebooks)의 
소스코드 내용을 참고해서 작성되었습니다.
자료를 공개한 저자에게 진심어린 감사를 전합니다.

**소스코드**

여기서 언급되는 코드를
[(구글 코랩) 머신러닝 모델 훈련 기법](https://colab.research.google.com/github/codingalzi/dlp2/blob/master/notebooks/NB-fundamentals_of_ml.ipynb)에서 
직접 실행할 수 있다.

**슬라이드**

본문 내용을 요약한 [슬라이드](https://github.com/codingalzi/dlp2/raw/master/slides/slides-fundamentals_of_ml.pdf)를 다운로드할 수 있다.

**주요 내용**

- 최적화, 일반화, 과대적합
- 모델 평가
- 모델 훈련 최적화
- 모델 일반화 성능 향상 기법

## 최적화, 일반화, 과대적합

### 머신러닝 모델 훈련의 핵심: 최적화대 일반화

머신러닝 모델 훈련의 주요 과제는 모델 훈련의 **최적화**<font size='2'>optimization</font>와 
모델 **일반화**<font size='2'>generalization</font> 사이의 적절한 관계 찾기이다.

- **최적화**: 훈련셋에 대해 가장 좋은 성능 이끌어내기
- **일반화**: 훈련 과정에서 보지 못한 데이터에 대한 성능 향상시키기

모델 훈련의 최적화는 데이터셋 전처리, 적절한 모델 구성과 모델의 하이퍼파라미터 설정 등을 통해 이루어진다.
반면에 모델 성능의 일반화는 훈련을 통해 조정할 수 있는 대상이 아니다.
하지만 모델 훈련의 최적화 과정에서 일부 설정을 조정하면 훈련된 모델의 일반화 성능을 끌어올릴 수 있다.

모델은 훈련을 많이 할 수록 일반적으로 훈련셋에 대해 보다 좋은 성능을 보인다.
즉, 최적화가 진행된다.
하지만 훈련을 많이 할 수록 새로운 데이터에 대한 성능인
일반화 성능은 점점 약해지는 과대적합 현상이 발생할 가능성이 높아지며
언젠가는 반드시 과대적합이 발생한다.
따라서 머신러닝 모델 훈련의 핵심은 과대적합 현상을 최대한 피하면서 최적화 훈련을 오래할 수 있는
모델 구성과 모델의 하이퍼파라미터 설정을 조정하는 일이다.

### 과대적합 대 과소적합

**과대적합**<font size='2'>overfitting</font>은 모델이 훈련셋에 너무 적응해서 훈련셋의 속성에 민감하게 반응하는 현상을 가리킨다.
과대적합이 발생하면 훈련중에 경험하지 못한 데이터에 대해 제대로 반응하지 못한다.

반면에 **과소적합**<font size='2'>underfitting</font>은 모델이 훈련셋의 속성을 아직 덜 파악한 상태를 의미한다.
보통 훈련 초반에 일어나는 현상이며, 모델이 훈련셋과 검증셋 모두에 대해 성능이 향상되는 과정에 해당한다.

또한 모델 설정이 잘못되어 모델 훈련이 전혀 진행되지 않는 경우도 과소적합에 해당한다.
예를 들어 언어 인식 등 매우 복잡한 문제를 단순한 선형회귀 모델로 
훈련시키려 하면 당연히 모델이 절대로 좋은 성능을 내지 못하는 과소적합 현상이 발생한다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/typical_overfitting.png" style="width:600px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

### 과대적합 발생 주요 요인

과대적합을 발생시키는 요인은 크게 세 가지로 나뉜다.

**첫째, 훈련셋에 포함된 노이즈**

적절하지 않은 데이터 또는 잘못된 라벨을 갖는 데이터 등을 **노이즈**<font size='2'>noise</font>라 부른다.

- 적절하지 않은 데이터: 다음 MNNIST 이미지들처럼 불분명하면 특성 파악이 어렵다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/fucked_up_mnist.png" style="width:500px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

- 잘못된 라벨: 예를 들어, 잘못 분류된 1처럼 생긴 이미지를 7로 잘못 분류할 가능성이 높아진다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/mislabeled_mnist.png" style="width:660px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

노이즈 등의 이상치<font size='2'>outlier</font>를 학습하면
아래 오른편 그림의 경우처럼 모델이 이상치의 특별한 특성을 학습하게 되어
새루운 데이터에 대한 예측 성능이 불안정해지게 된다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/outliers_and_overfitting.png" style="width:660px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

**둘째, 애매한 특성**

노이즈 등의 이상치가 전혀 없다 하더라도 특정 특성 영역에 대한 예측값이 여러 개의 값을 가질 수 있다. 

<div align="center"><img src="https://raw.githubusercontent.com/codingalzi/handson-ml3/master/jupyter-book/imgs/ch04/iris01.png" style="width:500px;"></div>

예를 들어, 붓꽃 데이터셋의 경우 꽃잎의 길이와 너비만을 활용해서는 
버시컬러<font size='2'>versicolor</font> 품종과 
버지니카<font size='2'>virginica</font> 품종의 완벽한 구분이
애초에 불가능하다.

<div align="center"><img src="https://codingalzi.github.io/handson-ml2/slides/images/ch05/homl05-03b.png" style="width:500px;"></div>

하지만 훈련을 오래 시키면 각 샘플의 특성을 해당 라벨의 고유의 특성으로
간주하는 정도까지 모델이 훈련되어 아래 오른편 그림과 같이
샘플의 특성에 너무 민감하게 작동한다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/HighResolutionFigures/figure_5-5.png" style="width:660px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

**셋째: 특성과 타깃 사이의 거짓 상관관계**

특성과 타깃 사이의 거짓 상관관계를 유발하는 여러 상황이 있다.

- 매우 드문 특성을 사용하는 데이터셋으로 훈련하는 경우

    {numref}`%s절 <sec:imdb>`의 이진 분류 모델의 훈련에 사용된
    IMDB 데이터셋에서 매우 낮은 빈도로 사용되는 단어를 훈련셋에서 포함시키는 경우
    어쩌다 한 번 사용되는 특성으로 인해 잘못된 판단이 유발될 수 있다.

    예를 들어, 에쿠아도르, 페루 등 안데스 산맥 지역에서 자라는 Cherimoya(체리모야) 라는
    과일 이름이 들어간 영화 후기가 단 하나만 있으면서 마침 부정적이었다면,
    분류 모델은 Cherimoya 단어가 들어간 영화 후기를 기본적으로 부정적으로 판단할 가능이 높아진다.

    <div align="center"><img src="https://raw.githubusercontent.com/codingalzi/dlp2/master/jupyter-book/imgs/cherimoya.jpg" style="width:300px;"></div>

    <p><div style="text-align: center">체리모야 열매</div></p>

    이렇듯 매우 매우 드물게 사용되는 특성은 과대적합을 유발한다. 
    앞서 사용 빈도에서 10,000등 안에 드는 단어만으로 작성된 영화 후기만을 대상으로 훈련시킨 이유가
    이런 가능성을 제한하기 위해서였다.

- 우연에 의한 경우

    자주 발생하는 특성이라 하더라도 우연히 잘못된 편견을 훈련중인 모델에 심어줄 수 있다.
    예를 들어, "너무" 라는 단어를 포함한 100개의 영화 후기 중에서 54%는 긍정,
    나머지 46%는 부정이었다면 훈련중인 모델은 "너무"라는 단어를 긍정적으로 평가할 가능성을 높힌다.
    하지만 "너무"라는 단어는 긍정적으로, 부정적으로 사용될 수 있기 때문에 이는 우연에 불과하다.

- 의미 없는 특성에 의한 경우

    아래 이미지는 MNIST 데이터셋에 **화이트 노이즈**<font size='2'>white noise</font>가 추가된 경우와
    단순히 여백이 추가된 경우의 훈련 샘플을 보여준다.

    <div align="center"><img src="https://raw.githubusercontent.com/codingalzi/dlp2/master/jupyter-book/imgs/ch05-mnist-noise.png" style="width:400px;"></div>

    <p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

    화이트 노이즈가 포함된 샘플들의 데이터셋으로 훈련시킨 모델과
    단순한 여백이 추가된 샘플들의 데이터셋으로 훈련시킨 모델의 성능을 비교하면
    화이트 노이즈가 포함된 훈련셋을 이용한 모델의 성능이 1% 정도 떨어진다.

    <div align="center"><img src="https://raw.githubusercontent.com/codingalzi/dlp2/master/jupyter-book/imgs/ch05-mnist-noise03.png" style="width:400px;"></div>

    이유는 모델이 화이트 노이즈에 특별한 의미를 부여하기 때문이며, 이로 인해 과대적합이
    보다 쉽게 발생한다.
    따라서 보다 효율적인 훈련을 위해 화이트 노이즈 등 과대적합을 유발하는
    특성을 미리 제거하여 모델에 유용한 특성만을 훈련에 사용해야 한다.
    하지만 유용한 특성을 선택하는 일이 기본적으로 불가능하거나 매우 어렵다.

:::{admonition} 화이트 노이즈
:class: note

프로그래밍 분야에서 화이트 노이즈<font size='2'>white noise</font>은
**무작위적으로 생성되었지만 전 영역에 걸쳐 고르게 퍼진 데이터셋**을 의미한다.
화이트 노이즈가 다른 데이터와 섞일 경우 화이트 노이즈를 분리하는 것은 원천적으로 불가능하다.
:::

## 모델 평가

검증셋을 활용하여 모델의 일반화 능력을 평가하는 방법을 소개한다.

### 훈련셋, 검증셋, 테스트셋

테스트셋은 모델 구성과 훈련에 전혀 관여하지 않아야 한다.
따라서 구성된 모델의 성능을 평가하려면 테스트셋을 제외한 다른 데이터셋이 필요한데
이를 위해 훈련셋의 일부를 검증셋으로 활용한다.

**모델 튜닝**

검증셋은 **훈련 과정 중에 모델의 일반화 성능을 테스트**하는 용도로 사용된다.
모델의 검증셋에 대한 성능 평가를 바탕으로
모델 구성과 모델의 **하이퍼파라미터**<font size='2'>hyperparameter</font> 설정을 조정한다. 
이처럼 검증셋을 활용하여 최적의 모델을 찾는 과정이 **모델 튜닝**<font size='2'>model tuning</font>이다.

**정보 유출**

모델 튜닝도 모델의 좋은 하이퍼파라미터를 찾아가는 일종의 **학습**이다. 
따라서 튜닝을 많이 하게되면 검증셋에 특화된 모델이 얻어질 가능성이 커진다.
즉, 검증셋에 과대적합된 모델이 훈련될 가능성이 높아진다.
이런 현상을 **정보 유출**이라 하는데,
이유는 튜닝을 하면 할 수록 검증셋에 대한 보다 많은 정보가 모델로 흘러 들어가기 때문이다.

:::{admonition} 하이퍼파라미터 대 파라미터
:class: info

하이퍼파라미터와 파라미터는 다르다. 
파라미터는 모델 훈련 중에 학습되는 가중치, 편향 등을 가리킨다.
:::

**모델 평가용 데이터셋 준비 관련 주의사항**

모델 훈련의 최적화를 위해 아래 세 가지 사항을 준수하면서 훈련셋, 검증셋, 테스트셋을 준비해야 한다. 

- **대표성**: 일반적으로 데이터셋을 무작위로 섞어 라벨이 적절한 비율로 섞인 
    훈련셋, 검증셋, 테스트셋을 구성해야 한다.
- **순서 준수**: 미래를 예측하는 모델을 훈련시킬 때, 테스트셋의 데이터는 훈련셋의 데이터보다
    시간상 뒤쪽에 위치하도록 해야 한다. 그렇지 않으면 미래 정보가 모델에 유출된다.
    즉, 데이터를 무작위로 섞어 훈련셋과 테스트셋으로 구분하는 일은 하지 않아야 한다. 
- **중복 데이터 제거**: 훈련셋과 테스트셋에 동일한 데이터가 들어가지 않도록 중복 데이터를 제거해야 한다.
    그렇지 않으면 중복된 데이터에 보다 민감하게 작동하는 공정하지 못한 모델 훈련이 발생할 수 있다.

### 검증셋 활용법

데이터셋을 훈련셋, 검증셋, 테스트셋으로 분류하여 모델 훈련을 진행하는
전형적인 방식 세 가지를 소개한다. 

**홀드아웃<font size='2'>hold-out</font> 검증**

훈련셋의 일부를 검증셋으로 지정하고 모델 튜닝에 활용하는 가장 일반적인 방법이다.
반면에 테스트셋은 모델 훈련에 절대로 활용하지 않고 훈련이 끝난 다음
실전에 배치하기 이전에 미리 실전 활용도를 평가하는 용도로만 사용한다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/holdout_validation.png" style="width:350px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

**K-겹 교차검증**

홀드아웃 검증은 하지만 데이터셋이 크지 않은 경우 사용하기 어렵다.
이유는 데이터셋 자체가 작기 때문에 훈련셋으로부터 검증셋을 분리하면 훈련셋이 더욱 작아져서
제대로된 훈련이 이뤄지기 어려울 수 있기 때문이다.
이런 경우 K-겹 교차검증이 권장된다.

K-겹 교차검증은
훈련셋을 K 개의 부분집합으로 분류한 다음에 한 개의 부분집합을 검증셋으로,
나머지늘 훈련셋으로 사용하는 방식을 K 번 반복하는 훈련법이다.
이때 검증셋으로 사용되는 부분집합은 매번 다르게 선택된다.

모델의 성능은 K개의 검증성능의 평균값으로 평가된다.
아래 그림은 3-겹 교차검증의 작동 과정을 보여준다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/k_fold_validation.png" style="width:650px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

필요에 따라 K-겹 교차검증을 반복 적용할 수 있다.
훈련셋의 크기가 너무 작거나 모델의 성능을 최대한 정확하게 평가하기 위해 사용된다.
대신 매번 훈련셋을 무작위로 섞은 뒤에 교차검증을 실행한다. 
최종 결과는 각 교차검증의 평균값을 사용한다. 
훈련 시간이 매우 오래 걸린다는 게 이 방법의 단점이다. 
K-겹 교차 검증을 P번 반복하면 총 `P * K` 개의 모델을 훈련시키게 된다.

### 모델 성능 평가의 기준선

모델 훈련이 시작되면 평가지표<font size='2'>metrics</font>를 지켜보는 일 이외에 할 수 있는 게 없다.
다만 훈련중에 검증셋에 대한 평가지표가 특정 기준선 이상으로 좋아지는지를 확인한다.

예를 들어 지금까지 살펴봤던 모델들의 기준선은 다음과 같다.

- MNIST 데이터셋: 10%의 정확도
- IMDB 데이터셋: 50%의 정확도
- 로이터 통신 기사: 18-19%의 정확도. 기사들이 균등하게 분포되어 있지 않음.

모델 훈련을 시작할 때의 기본 목표는 기준선을 넘기는 성능을 가진 모델 훈련에 둔다.
모델 훈련 동안 기준선을 넘기지 못한다면
무언가 잘못된 모델 구성과 설정을 사용하고 있을 가능성이 크다.

## 모델 훈련 최적화

모델 훈련을 최적화하려면 모순적이게도 먼저 과대적합을 달성해야 한다.
이유는 과대적합이 나타나야만 과대적합의 경계를 알아내서 모델 훈련을
언제 멈추어야 하는지 알 수 있기 때문이다. 
일단 과대적합의 경계를 찾은 다음에 일반화 성능 향상을 목표로 삼는다.

모델 훈련 중에 발생하는 문제는 일반적으로 다음 세 종류이다. 

- 첫째, 훈련셋의 손실값이 줄어들지 않아 훈련이 제대로 진행되지 않는 경우
- 둘째, 훈련셋의 손실값은 줄어들지만 검증셋의 성능은 평가 기준선을 넘지 못하는 경우
- 셋째, 훈련셋과 검증셋의 평가가 기준선을 넘어 계속 좋아지지만 과대적합이 발생하지 않아
    계속해서 과소적합 상태로 머무는 경우
    
언급된 문제들을 해결하기 위해 일반적으로 모델의 보다 적절한 하이퍼파라미터 선택, 
보다 많은 양질의 데이터 수집, 다른 종류의 모델 선택, 규제 활용 등
다양한 기법을 적용한다. 

**첫째 경우: 경사하강법 관련 하이퍼파라미터 조정**

훈련셋의 손실값이 줄어들지 않거나 진동하는 등 훈련이 제대로 이루어지지 않는 경우는
기본적으로 경사하강법이 제대로 작동하지 않아서이다.
이럴 때는 보통 학습률과 배치 크기를 조정하면 해결된다.

*학습률 조정*

- 매우 큰 학습률을 사용하는 경우: 모델이 제대로 학습되지 않는다.

<div align="center"><img src="https://codingalzi.github.io/handson-ml2/slides/images/ch04/homl04-03.png" style="width:550px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://github.com/ageron/handson-ml2">핸즈온 머신러닝(2판), 4장</a>&gt;</div></p>

- 매우 작은 학습률을 사용하는 경우: 모델이 너무 느리게 학습된다.

<div align="center"><img src="https://codingalzi.github.io/handson-ml2/slides/images/ch04/homl04-02.png" style="width:550px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://github.com/ageron/handson-ml2">핸즈온 머신러닝(2판), 4장</a>&gt;</div></p>

- 적절한 학습률을 사용하는 경우: 모델이 적절한 속도로 학습된다.

<div align="center"><img src="https://codingalzi.github.io/handson-ml2/slides/images/ch04/homl04-01.png" style="width:550px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://github.com/ageron/handson-ml2">핸즈온 머신러닝(2판), 4장</a>&gt;</div></p>

*배치 크기 조정*

학습률 이외에 배치크기를 키우면 보다 안정적으로 훈련이 된다.
단, 배치 크기를 너무 크게 지정하면 계산량이 많아져서 훈련 시간이 오래 걸릴 수 있다.
아래 그림은 배치 크기가 클 수록 보다 부드럽게 
손실값이 보다 부드럽게 특정 값에 수렴하는 것, 즉 모델이 보다 일관되게 학습되는 것을 보여준다.

<div align="center"><img src="https://codingalzi.github.io/handson-ml2/slides/images/ch04/homl04-05.png" style="width:550px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://github.com/ageron/handson-ml2">핸즈온 머신러닝(2판), 4장</a>&gt;</div></p>

**둘째 경우: 보다 적절한 모델 사용**

훈련은 잘 진행되는데 검증셋에 대한 성능이 좋아지지 않는다면 다음 두 가지 경우를 의심해 보아야 한다. 

- 훈련셋이 적절한지 않은 경우
    - 예제: 라벨이 무작위로 섞인 MNIST 데이터셋
- 사용하는 모델이 적절하지 않은 경우
    - 예제: 선형 분류가 불가능한 데이터셋에 선형분류 모델을 적용하는 경우
    - 예제: 시계열 데이터 분석에 앞서 살펴본 `Sequential` 모델을 사용하는 경우
    
문제 해결에 적절한 모델을 훈련시켜야 한다.
앞으로 주어진 문제에 따른 다양한 모델 구성과 훈련방법을 살펴볼 것이다.

**셋째 경우: 모델의 정보 저장 능력 조정**

모델의 훈련셋/검증셋의 평가지표가 계속 향상되지만 과대적합이 발생하지 않는 경우 
기본적으로 모델의 정보 저장 능력을 키워야 한다. 
즉, 신경망 모델의 은닉층 또는 층에 사용되는 유닛의 수를 증가시켜서
모델이 보다 많은 정보를 처리하여 보다 적절한 방식으로 값을 변환할 수 있도록 한다.

## 모델 일반화 성능 향상 기법

모델 훈련이 어느 정도 잘 진행되어 일반화 성능이 향상되고 과대적합이 발생하기 시작하면
모델의 일반화 성능을 극대화하는 방법에 집중한다.
일반적으로 다음 두 가지 사항이 모델의 일반화 성능에 도움된다.

- 조기 종료
- 규제

### 조기 종료

모델 훈련 중에 훈련셋에 대한 성능은 계속 좋아지지만 
검증셋에 대한 성능이 더 이상 좋아지지 않는 순간에 모델 훈련을 멈추는 것이 
**조기 종료**(early stopping)이다.
이를 위해 에포크마다 모델의 검증셋에 대한 성능을 측정하여 가장 좋은 성능의 모델을 기억해 두고,
더 이상 좋아지지 않으면 그때까지 기록된 최적의 모델을 
최종 모델로 사용한다. 

<div align="center"><img src="https://raw.githubusercontent.com/codingalzi/dlp2/master/jupyter-book/imgs/ch05-early-stopping.png" style="width:600px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

케라스의 경우 `EarlyStopping` 이라는 
**콜백**<font size='2'>callback</font> 기능을 이용하여 조기 종료 기능을 간단하게 지정할 수 있다.
다양한 콜백 기능에 대해서는 {numref}`%s장 <ch:working_with_keras>` 자세히 다룬다.

### 규제: 드롭아웃

모델이 훈련셋에 너무 익숙해지지 않도록 방해하는 것을
규제라 부른다.
모델 규제를 위해 **드롭아웃**<font size='2'>drop out</font> 기법이 많이 적용된다.
드롭아웃은 무작위로 선택된 일정한 비율의 유닛을 끄는 것을 의미하며,
해당 유닛에 저장된 값을 0으로 처리한다. 

아래 그림은 50%의 드롭아웃을 층의 출력값에 적용하는 과정을 보여준다.
출력값의 50%를 0으로 처리한 다음에 출력 텐서를 0.5로 나눈다.
즉 2를 곱해준다.
이유는 드롭아웃 기능은 훈련에만 적용하며 실전에서는 사용되지 않기에 
출력값의 최종 크기를 훈련일 때와 아닐 때 비슷하게 만들어주기 위해서이다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/Figures/05-20.png" style="width:500px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

케라스에서는 드롭아웃 적용을 위해 적절한 드롭아웃 비율을 답은 드롭아웃 층 `Dropout`을 활용한다.
아래 그래프는 IMDB 영화 후기 분류 모델 대상으로 50%의 드롭아웃을 적용하여 훈련하면
검증셋에 대한 손실값이 보다 천천히 증가함을 보여준다. 
즉, 모델의 과대적합이 보다 늦게, 보다 약하게 발생한다.

<div align="center"><img src="https://drek4537l1klr.cloudfront.net/chollet2/v-7/Figures/original_model_vs_dropout_regularized_model_imdb.png" style="width:500px;"></div>

<p><div style="text-align: center">&lt;그림 출처: <a href="https://www.manning.com/books/deep-learning-with-python-second-edition">Deep Learning with Python(2판)</a>&gt;</div></p>

## 연습문제

1. [(실습) 머신러닝 모델 훈련 기법](https://colab.research.google.com/github/codingalzi/dlp2/blob/master/excs/exc-fundamentals_of_ml.ipynb)